# Accessing geospatial data the sort of easy way (Julia)


The access to geospatial data has changed significantly over the past decade. Data has traditionally been accessed by downloading several files to a local computer, then analyzing them with software or programming languages. It has always been difficult to access analysis-ready datasets due to the diversity of data formats (NetCDF, Grib2, Geotiff, Shapefile, etc.) and the variety of access protocols from different providers (Opendap, HTTPS, SFTP, WPS, API Rest, Datamarts, etc.). Beyond that, with the ever-increasing size of geospatial datasets, most modern datasets cannot even fit on a local computer, limiting science's progress

The datasets presented here are large-scale analysis-ready cloud optimized (ARCO). In order to implement an entry point for a list of datasets, we have followed the methodology developed by the Pangeo community, which combines multiple technologies:
- Data Lake (or S3, Azure Data Lake Storage, GCS, etc.) : distributed file-object storage
- [Zarr](https://zarr.readthedocs.io/en/stable/) (or alternatively TileDB, COGs) : chunked N-dimensionnal array formats
- [Dask](https://docs.dask.org/en/stable/)  (or alternatively Spark, Ray, Distributed) : distributed computing and lazy loading
- [Intake](https://intake.readthedocs.io/en/latest) Catalogs (or alternatively STAC) : a general interface for loading different data formats, mostly but not limited to spatiotemporal assets

For more information, please refer to the [pangeo's website](https://pangeo.io/)

It is important to note that most datasets are language-agnostic, which means they can be accessed using a variety of programming languages, including Zarr, netcdfs (kerchunk), geojson, etc. (Python, Julia, Javascript, C, etc.).


In [ ]:
import Pkg
Pkg.add("Zarr")
Pkg.add("YAXArrays")
Pkg.add("Plots")

In [17]:
using Zarr, YAXArrays, Plots

Please refer to the python document (Accessing geospatial data the easy way (Python)) for details about using the Intake catalog. From the catalogs, you can fetch urls associated with each dataset and pass them to the appropriate library. In essence, this is what Intake catalogs do in Python and should an equivalent library become available in Julia, we would recommand using it instead.

In [3]:
store = "https://s3.us-east-1.wasabisys.com/era5/world/reanalysis/single-levels/zarr/timeseries/archive"

g = open_dataset(zopen(store, consolidated=true))
c = Cube(g)

YAXArray with the following dimensions
longitude           Axis with 1440 Elements from -180.0 to 179.75
latitude            Axis with 721 Elements from 90.0 to -90.0
time                Axis with 368184 Elements from 1979-01-01T00:00:00 to 2020-12-31T23:00:00
Variable            Axis with 2 elements: tp t2m 
units: K
Total size: 2.78 TB


In [21]:
c[Variable="t2m"](:,0,0)

LoadError: MethodError: objects of type YAXArray{Float32, 3, DiskArrays.SubDiskArray{Float32, 3}, Vector{CubeAxis}} are not callable

In [37]:
da = c[Variable = "t2m", longitude = -75, latitude = 40]


YAXArray with the following dimensions
time                Axis with 368184 Elements from 1979-01-01T00:00:00 to 2020-12-31T23:00:00
units: K
Total size: 1.4 MB


In [50]:
@time begin
plot(da.time, da.data, xlabel="time",ylabel="t2m", leg = false)
end

  9.847662 seconds (157.36 k allocations: 785.525 MiB, 0.45% gc time)
